In [11]:
import requests
import pandas as pd
import os
from dotenv import load_dotenv

load_dotenv()

LUABASE_API_KEY = os.getenv('LUABASE_USER_API_KEY')

In [3]:
tables = [
    {
        'name': 'blocks',
        'dt': 'timestamp',
    },
    {
        'name': 'transactions',
        'dt': 'block_timestamp',
    },
    {
        'name': 'logs',
        'dt': 'block_timestamp',
    },
    {
        'name': 'events',
        'dt': 'block_timestamp',
    },
]

In [5]:
def get_table_dates(table_dict):
    url = 'https://q.luabase.com/run'
    table = table_dict['name']
    table_dt = table_dict['dt']
    sql = f'''
    select 
    toYYYYMM({table_dt}) as mdt,
    toYYYYMMDD({table_dt}) as ddt,
    count() as ct
    from ethereuam.{table} as t
    group by ddt, mdt
    order by ddt desc
    '''

    payload = {
        'block': {
            'details': {
                'sql': sql,
            },
        },
        'api_key': LUABASE_API_KEY,
    }
    headers = {'content-type': 'application/json'}
    response = requests.request('POST', url, json=payload, headers=headers)
    data = response.json()
    return data

In [6]:
for table in tables:
    print('gettting dates for', table['name'])
    table['dates_to_get'] = get_table_dates(table)

gettting dates for blocks
gettting dates for transactions
gettting dates for logs
gettting dates for events


In [7]:
def get_table_days(table_dict, num_days_to_get, bucket_name, integration_id):
    url = 'https://q.luabase.com/run'
    # https://q.luabase.com/run/async

    table = table_dict['name']
    table_dt = table_dict['dt']
    # start at 1 to remove incomplete current day
    for row in table_dict['dates_to_get']['data'][1:num_days_to_get]:
        ddt = row['ddt']
        sql = f'''
        select *
        from ethereum.{table} as t
        where toYYYYMMDD({table_dt}) = {ddt}
        '''
        print('sql: ', sql)
        fname = f'{table}_{ddt}'

        payload = {
            'block': {
                'data_uuid': fname,
                'details': {
                    'sql': sql,
                    'destination': {
                        "type": "s3",
                        "paused": False,
                        "fileName": fname,
                        "ifExists": "replace",
                        "bucketName": bucket_name,
                        "integrationId": integration_id,
                    },
                },
            },
            'api_key': LUABASE_API_KEY,
        }
        headers = {'content-type': 'application/json'}
        response = requests.request('POST', url, json=payload, headers=headers)
        data = response.json()
        print('done: ', ddt, response)
        return data

In [ ]:
# lua-test-eth-full-sync

for table in tables:
    res = get_table_days(table, 3, 'luabase-not-public', '8e86ae3479be49bfb5fdc843c6c6838f')
    print(res)

In [9]:
url = 'https://q.luabase.com/run'
bucket_name = 'lua-test-eth-full-sync'
table_dict = {
    'name': 'blocks',
    'dt': 'timestamp',
}
table = table_dict['name']
table_dt = table_dict['dt']
integration_id = '8e86ae3479be49bfb5fdc843c6c6838f'
ddt = 20220801
sql = f'''
select *
from ethereum.{table} as t
where toYYYYMMDD({table_dt}) = {ddt}
'''
print('sql: ', sql)
fname = f'{table}_{ddt}'


payload = {
    'block': {
        'data_uuid': fname,
        'details': {
            'sql': sql,
            'destination': {
                "type": "s3",
                "paused": False,
                "fileName": fname,
                "ifExists": "replace",
                "bucketName": bucket_name,
                "integrationId": integration_id,
            },
        },
    },
    'api_key': LUABASE_API_KEY,
}
headers = {'content-type': 'application/json'}
response = requests.request('POST', url, json=payload, headers=headers)
data = response.json()
print('done: ', ddt, response)

sql:  
select *
from ethereum.blocks as t
where toYYYYMMDD(timestamp) = 20220801

done:  20220801 <Response [422]>


In [10]:
data

{'detail': [{'loc': ['body', 'api_key'],
   'msg': 'field required',
   'type': 'value_error.missing'}]}

In [12]:
LUABASE_API_KEY

In [13]:
import requests

url = "https://api.luabase.com/run"

payload = {
"uuid": "74782438fd6b40129d71c3f64cfcd589",
"parameters": {}
}
headers = {"content-type": "application/json"}
response = requests.request("POST", url, json=payload, headers=headers)
data = response.json()


In [14]:
data

{'meta': [{'name': 'number', 'type': 'UInt64'},
  {'name': 'hash', 'type': 'String'},
  {'name': 'timestamp', 'type': 'DateTime'},
  {'name': 'size', 'type': 'UInt64'},
  {'name': 'transaction_count', 'type': 'UInt32'},
  {'name': 'transactions_root', 'type': 'String'},
  {'name': 'miner', 'type': 'String'},
  {'name': 'nonce', 'type': 'String'},
  {'name': 'logs_bloom', 'type': 'String'},
  {'name': 'state_root', 'type': 'String'},
  {'name': 'difficulty', 'type': 'UInt64'},
  {'name': 'total_difficulty', 'type': 'UInt128'},
  {'name': 'parent_hash', 'type': 'String'},
  {'name': 'sha3_uncles', 'type': 'String'},
  {'name': 'receipts_root', 'type': 'String'},
  {'name': 'gas_used', 'type': 'UInt64'},
  {'name': 'gas_limit', 'type': 'UInt64'},
  {'name': 'base_fee_per_gas', 'type': 'Nullable(UInt64)'},
  {'name': 'extra_data', 'type': 'String'}],
 'data': [{'number': 0,
   'hash': '0xd4e56740f876aef8c010b86a40d5f56745a118d0906a34e69aec8c0db1cb8fa3',
   'timestamp': '1970-01-01 00:00:00

In [15]:
LUABASE_API_KEY